In [ ]:
# ..... Knight-Schrijver et al data ..... #
# integrated fetal + adult HCA data - 60k cells

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)

In [3]:
# subset to fetal 30k cells only
sch = readRDS('~/septation/knight_fetal_adult_human_heart.rds')
sch <- sch[,(sch$cell_states=='foetal')]
sch

An object of class Seurat 
27473 features across 30889 samples within 1 assay 
Active assay: RNA (27473 features, 0 variable features)
 1 dimensional reduction calculated: umap

In [8]:
sch@meta.data[1,]

nCount_RNA nFeature_RNA age_group cell_source
GCGCGATCATACGCCG-alexsc 7069       2319         NA        F - Apex   
                        cell_states sample age.order age.days.GA size.CRL
GCGCGATCATACGCCG-alexsc foetal      alexsc F5        67          NA      
                        size.NRL ⋯ suspension_type is_primary_data cell_type 
GCGCGATCATACGCCG-alexsc NA       ⋯ cell            TRUE            fibroblast
                        assay     disease organism     sex    tissue       
GCGCGATCATACGCCG-alexsc 10x 3' v2 normal  Homo sapiens female apex of heart
                        self_reported_ethnicity
GCGCGATCATACGCCG-alexsc unknown                
                        development_stage                       
GCGCGATCATACGCCG-alexsc 10th week post-fertilization human stage

In [11]:
# cell types in clusters.low.res, clusters.res.2, clusters.res.3
c1 = unique(sch$clusters.res.2)
c1
length(c1)

[1] Fibroblasts              Immature_other           Smooth_Muscle_Cells     
 [4] Pericytes                Endocardial              Endothelial_Other       
 [7] Immature_Cardiomyocytes  Cardiomyocytes           Endothelial_Capillaries 
[10] Myeloid_Immune_Cells     Endothelial_Venous       Endothelial_Arterial    
[13] Epicardium_Meso          Epicardium_FB-like       Epicardium_Proliferating
[16] Lymphoid_Immune_Cells    Adipocytes               Neuronal_Cells          
[19] Pericytes_Stromal       
19 Levels: Adipocytes Cardiomyocytes Endocardial ... Smooth_Muscle_Cells

[1] 19

In [30]:
id = 19
c1[id]
unique(sch$clusters.res.3[sch$clusters.res.2==c1[id]])

[1] Pericytes_Stromal
19 Levels: Adipocytes Cardiomyocytes Endocardial ... Smooth_Muscle_Cells

[1] Pericytes_Stromal
34 Levels: Adipocytes Atrial_Cardiomyocytes B_cells ... Ventricular_Cardiomyocytes

In [31]:
# get SCE object
sce2 = SingleCellExperiment(list(counts = GetAssayData(sch, 'counts')),
                            colData = DataFrame(sch@meta.data))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))

In [32]:
# get cell type markers on foetal data
markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$clusters.res.3, 
                          group_labels = sce2$clusters.res.2)
head(markers)

Warning message in FUN(X[[i]], ...):
“Skipping group Smooth_Muscle_Cells: only 1 cluster (Smooth_Muscle_Cells).”
Warning message in FUN(X[[i]], ...):
“Skipping group Pericytes: only 1 cluster (Pericytes).”
Warning message in FUN(X[[i]], ...):
“Skipping group Endocardial: only 1 cluster (Endocardial).”
Warning message in FUN(X[[i]], ...):
“Skipping group Endothelial_Other: only 1 cluster (Endothelial_Other).”
Warning message in FUN(X[[i]], ...):
“Skipping group Immature_Cardiomyocytes: only 1 cluster (Immature_Cardiomyocytes).”
Warning message in FUN(X[[i]], ...):
“Skipping group Endothelial_Capillaries: only 1 cluster (Endothelial_Capillaries).”
Warning message in FUN(X[[i]], ...):
“Skipping group Endothelial_Venous: only 1 cluster (Endothelial_Venous).”
Warning message in FUN(X[[i]], ...):
“Skipping group Endothelial_Arterial: only 1 cluster (Endothelial_Arterial).”
Warning message in FUN(X[[i]], ...):
“Skipping group Epicardium_Meso: only 1 cluster (Epicardium_Meso).”
Warning message

group       cell_type       gene            fold_change auroc     log_fdr  
1 Fibroblasts Fibroblast-like ENSG00000104332 4.021162    0.8242303 -647.8685
2 Fibroblasts Fibroblast-like ENSG00000120885 4.931605    0.7705290 -449.5981
3 Fibroblasts Fibroblast-like ENSG00000116132 3.464489    0.7562956 -403.7918
4 Fibroblasts Fibroblast-like ENSG00000122641 3.651482    0.7350450 -339.0578
5 Fibroblasts Fibroblast-like ENSG00000100300 5.633067    0.7315895 -329.1411
6 Fibroblasts Fibroblast-like ENSG00000133169 9.188654    0.7162512 -286.4389
  population_size population_fraction average_expression se_expression
1 2348            0.5581174           1576.0145          29.405917    
2 2348            0.5581174            504.6701          11.497139    
3 2348            0.5581174            370.5153           8.155818    
4 2348            0.5581174            303.8144           7.830567    
5 2348            0.5581174            231.9225           6.338491    
6 2348            0.5581174            269.8983           8.876934    
  detection_rate fold_change_detection precision recall   
1 0.8854344      2.624605              0.7685767 0.8854344
2 0.7040034      3.006939              0.7920460 0.7040034
3 0.7176320      3.044114              0.7940622 0.7176320
4 0.6218058      4.093191              0.8385985 0.6218058
5 0.5711244      4.567482              0.8530534 0.5711244
6 0.4923339      7.345147              0.9038311 0.4923339

In [33]:
# convert gene names to symbols
ginfo = read.delim('/data/CoCoCoNet/geneInfo/human_info.csv', sep = ',')
ginfo[1,]

EntrezID  EnsemblID       GeneSymbol LocusTag Synonyms
1 100287102 ENSG00000223972 DDX11L1    NA       NA      
  dbXrefs                                   Chromosome Type   UniProtID
1 |HGNC:HGNC:37102|Ensembl:ENSG00000223972| 1          pseudo NA       
  UniProtID2 OrthoID NetworkIDs     
1 NA         NA      ENSG00000223972

In [34]:
# remove genes w/o symbols
markers$gene <- ginfo$GeneSymbol[match(markers$gene, ginfo$EnsemblID)]
dim(markers)
markers <- markers[!is.na(markers$gene),]
dim(markers)

[1] 604406     14

[1] 455400     14

In [35]:
head(markers[markers$cell_type=='Fibroblasts',])
head(markers[markers$cell_type=='Cardiomyocytes',])

group       cell_type   gene     fold_change auroc     log_fdr  
1 Fibroblasts Fibroblasts SCN7A    7.536470    0.7657756 -434.1200
2 Fibroblasts Fibroblasts DCN      2.697889    0.7638538 -428.0657
3 Fibroblasts Fibroblasts TCF21    3.543116    0.7425419 -361.2187
4 Fibroblasts Fibroblasts COLEC11  8.126321    0.7153363 -284.0825
5 Fibroblasts Fibroblasts TMSB4X   1.947135    0.7110391 -272.8414
6 Fibroblasts Fibroblasts SERPINE2 3.246704    0.7067351 -261.8529
  population_size population_fraction average_expression se_expression
1 1859            0.4418826            534.5375          17.034346    
2 1859            0.4418826           2140.8305          45.839618    
3 1859            0.4418826            654.5267          14.688772    
4 1859            0.4418826            255.8069           8.626622    
5 1859            0.4418826           4359.4479          74.739818    
6 1859            0.4418826            703.8845          19.642739    
  detection_rate fold_change_detection precision recall   
1 0.6401291      4.3338989             0.7752443 0.6401291
2 0.8423884      1.7289731             0.5780731 0.8423884
3 0.7315761      1.7986013             0.5877269 0.7315761
4 0.5185584      4.5124175             0.7824675 0.5185584
5 0.9494352      0.9726606             0.4350505 0.9494352
6 0.6966111      1.5418590             0.5498938 0.6966111

group cell_type gene fold_change auroc log_fdr population_size
     population_fraction average_expression se_expression detection_rate
     fold_change_detection precision recall

In [36]:
# save marker list
export_meta_markers(markers, "Knight-Schrijver_celltype_markers_res3.csv", names(markers))